##### 1. Взять корпус текстов по вашему проекту или выбрать любой корпус текстов и рассказать, октуда вы его взяли и почему именно его (ответ "потому что он мне понравился" тоже валиден):
##### Он должен быть на русском (иное обсуждаемо, если корпус взят в рамках проекта) и содержать не меньше тысячи записей (абзацев, текстов, предложений etc).
##### Если корпус не по проекту, то:
##### Это может быть часть любого открытого корпуса, результат краулинга или даже генерации с помощью модели.
##### Будет здорово, если он будет тематический (машины, лингвистика, литератруа etc.), но не обязательно.

Я выбрала датасет русской Википедии. Он мне кажется подходящим. А еще я не смогла найти достаточное количество корпусов на русском языке, поэтому пришлось брать Википедию. А еще в этом корпусе 6 тысяч строк и он на русском.  

In [61]:
#все import'ы здесь
import pandas as pd
import re
import nltk
from nltk.corpus import stopwords
import pymorphy2
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.metrics.pairwise import cosine_similarity
from sklearn.metrics import precision_score, recall_score, f1_score
import pickle
import os
import torch
from transformers import BertTokenizer, BertModel
import numpy as np
import time


In [19]:
wiki_df = pd.read_json("hf://datasets/Den4ikAI/russian_cleared_wikipedia/wiki_dataset.json", lines=True)

In [20]:
wiki_df.head()

sample
0  Ева  — в авраамических религиях — праматерь вс...
1  Около 40 видов вечнозелёных высоких деревьев с...
2  Персонаж дуалистического космогонического мифа...
3  Аа:Аббревиатуры:Кирилицей:Латиницей:А. А. — со...
4                          Испанская фамилия:Другое:

#### **2. (1 балл) Провести предобработку текста так, чтобы это было логично при выбранном методе векторизации (объясните, почему выбрали то, что выбрали):**
- лемматизация
- чистка от пунктуации и стоп-слов
- что-то еще, что вы считаете нужным

In [21]:
import nltk
import pymorphy2
import re
from nltk.corpus import stopwords

nltk.download('stopwords')
russian_stopwords = set(stopwords.words("russian"))
morph = pymorphy2.MorphAnalyzer()

def preprocess_text(text):
    # Приведение к нижнему регистру
    text = text.lower()
    
    # Удаление только пунктуации (оставляем числа)
    text = re.sub(r'[^\w\s]', '', text)
    
    words = text.split()
    
    # Лемматизация и удаление стоп-слов
    processed_words = []
    for word in words:
        if word not in russian_stopwords:
            lemma = morph.parse(word)[0].normal_form  # можно заменить на стемминг, если нужна скорость
            processed_words.append(lemma)
    
    return ' '.join(processed_words)


[nltk_data] Downloading package stopwords to
[nltk_data]     C:\Users\Zaxarova\AppData\Roaming\nltk_data...
[nltk_data]   Unzipping corpora\stopwords.zip.


In [22]:
#применение функции
wiki_df['cleaned_text'] = wiki_df['sample'].apply(preprocess_text)
print(wiki_df['cleaned_text'])


0       ева авраамический религия праматерь человек пе...
1       около 40 вид вечнозелёный высокий дерево краси...
2       персонаж дуалистический космогонический миф им...
3       аааббревиатурыкирилицейлатиницей сокращение пр...
4                                 испанский фамилиядругий
                              ...                        
6279    1972 год посёлок носить название сигоу переиме...
6280    этимологиястроениепредставитель род дерево выс...
6281    ясин али иракский футболист вратарь иракский к...
6282    ясли христов ясли который предание положить мл...
6283    реакция критикиальбом получить положительный о...
Name: cleaned_text, Length: 6284, dtype: object


#### **3. (2 балла) Реализовать индекссацию двумя различными (!) способами. При этом результат индексации должен куда-то сохраняться, а не пересчитываться заново при каждом запуске программы (и тем более при каждом запросе!)**

 **Способ на основе статистики (частоты, tf-idf, bm25 etc.)**

 **Способ на основе эмбеддингов (word2vec, bert etc.)**

#### **TF_IDF**

In [23]:
#объект TF-IDF векторизатора
tfidf_vectorizer = TfidfVectorizer()

#текст -> вектор
tfidf_matrix = tfidf_vectorizer.fit_transform(wiki_df['cleaned_text'])
print(tfidf_matrix.shape)  

(6284, 236770)


In [24]:
#сохраняю данные tf-idf в pickle
with open('tfidf_vectorizer.pkl', 'wb') as f:
    pickle.dump(tfidf_vectorizer, f)

In [25]:
if os.path.exists('tfidf_vectorizer.pkl'):
    with open('tfidf_vectorizer.pkl', 'rb') as f:
        tfidf_vectorizer = pickle.load(f)
    print("Файл найден")
else:
    print("Файл tfidf_vectorizer.pkl не найден.")


Файл найден


In [26]:
with open('tfidf_vectorizer.pkl', 'rb') as f:
    tfidf_vectorizer = pickle.load(f)
print(tfidf_vectorizer.get_feature_names_out())
print(tfidf_vectorizer.idf_)
print(tfidf_vectorizer.vocabulary_)

['00' '000' '0000' ... 'ꙁобразный' '𐤁𐤀𐤓𐤕' '𐤇𐤍𐤁𐤏𐤋']
[7.80001097 4.15493414 8.64730883 ... 9.05277394 9.05277394 9.05277394]
{'ева': 78238, 'авраамический': 28095, 'религия': 175855, 'праматерь': 162780, 'человек': 225417, 'первый': 151065, 'женщина': 80545, 'жена': 80496, 'адам': 28970, 'создать': 191445, 'ребро': 174716, 'мать': 119060, 'каин': 94643, 'авель': 27847, 'сифабиблейский': 187904, 'рассказ': 173722, 'сотворение': 193026, 'грехопадение': 66785, 'изгнание': 88080, 'рай': 172657, 'породить': 160350, 'обширный': 140004, 'литература': 113552, 'апокрифический': 33747, 'характераэтимологиятрадиционный': 219887, 'этимология': 234236, 'возводить': 52780, 'имя': 89869, 'еврейский': 78433, 'хай': 219412, 'жизнь': 81149, 'современный': 191188, 'исследователь': 92838, 'предполагать': 163181, 'связь': 184046, 'финикийский': 216826, 'хвт': 220398, 'арамейский': 34120, 'хевъть': 220416, 'означать': 141784, 'змеяаналогичный': 86263, 'євг': 236623, 'встречаться': 55857, 'ипатьевский': 91671,

In [27]:
#сохраняю данные tf-idf в pickle
with open('tfidf_matrix.pkl', 'wb') as f:
    pickle.dump(tfidf_matrix, f)
if os.path.exists('tfidf_matrix.pkl'):
    with open('tfidf_matrix.pkl', 'rb') as f:
        tfidf_matrix = pickle.load(f)
    print("Файл найден")
else:
    print("Файл tfidf_matrix.pkl не найден.")

Файл найден


TF-IDF индексация:

1) Мы используем TfidfVectorizer для создания матрицы TF-IDF. Она превращает тексты в числовые векторы, учитывая частоту слов в документе и их редкость в корпусе.
2) Сохранение модели и самой матрицы происходит с помощью модуля pickle, чтобы при каждом запуске программы индексация не пересчитывалась заново.

#### **BERT**

In [28]:
tokenizer = BertTokenizer.from_pretrained('DeepPavlov/rubert-base-cased')
model = BertModel.from_pretrained('DeepPavlov/rubert-base-cased')

def get_bert_embeddings(texts):
    embeddings = []

    for text in texts:
        inputs = tokenizer(text, return_tensors='pt', padding=True, truncation=True, max_length=512)
        with torch.no_grad():
            outputs = model(**inputs)
        
        cls_embedding = outputs.last_hidden_state[:, 0, :].squeeze().numpy()
        embeddings.append(cls_embedding)
    
    return np.array(embeddings)

#применение BERT'а
bert_embeddings = get_bert_embeddings(wiki_df['cleaned_text'])

C:\Users\Zaxarova\AppData\Roaming\Python\Python310\site-packages\huggingface_hub\file_download.py:147: UserWarning: `huggingface_hub` cache-system uses symlinks by default to efficiently store duplicated files but your machine does not support them in C:\Users\Zaxarova\.cache\huggingface\hub\models--DeepPavlov--rubert-base-cased. Caching files will still work but in a degraded version that might require more space on your disk. This warning can be disabled by setting the `HF_HUB_DISABLE_SYMLINKS_WARNING` environment variable. For more details, see https://huggingface.co/docs/huggingface_hub/how-to-cache#limitations.
To support symlinks on Windows, you either need to activate Developer Mode or to run Python as an administrator. In order to activate developer mode, see this article: https://docs.microsoft.com/en-us/windows/apps/get-started/enable-your-device-for-development
  warnings.warn(message)
Some weights of the model checkpoint at DeepPavlov/rubert-base-cased were not used when in

In [29]:
with open('bert_embeddings.pkl', 'wb') as f:
    pickle.dump(bert_embeddings, f)

In [30]:
import os
if os.path.exists('bert_embeddings.pkl'):
    with open('bert_embeddings.pkl', 'rb') as f:
        tfidf_vectorizer = pickle.load(f)
    print("Файл найден")
else:
    print("Файл bert_embeddings.pkl не найден.")

Файл найден


In [31]:
#размер эмбеддингов
print(bert_embeddings.shape)

(6284, 768)


Модель: 
1) Мы используем модель ruBERT (DeepPavlov/rubert-base-cased), которая хорошо обучена на русскоязычных текстах. Мы загружаем токенизатор и модель с помощью библиотеки transformers.

Токенизация и преобразование текста в эмбеддинги:
1) Текст токенизируется (разбивается на слова и символы).
2) BERT принимает токенизированные тексты и возвращает эмбеддинги. Мы используем эмбеддинг специального CLS-токена, который обычно служит для представления всего предложения.

Сохранение: 

Эмбеддинги сохраняются в файл с помощью библиотеки pickle, чтобы их можно было загрузить при повторном запуске программы.

#### **4. (2 балла) Реализовать поиск: на входе текст запроса и вариант индекса, на выходе топ подходящих документов**

In [59]:
with open('tfidf_vectorizer.pkl', 'rb') as f:
    tfidf_vectorizer = pickle.load(f)

with open('tfidf_matrix.pkl', 'rb') as f:
    tfidf_matrix = pickle.load(f)

with open('bert_embeddings.pkl', 'rb') as f:
    bert_embeddings = pickle.load(f)

# Функция для поиска по TF-IDF
def search_tfidf(query, tfidf_vectorizer, tfidf_matrix, top_n=5):
    # Преобразуем запрос в векторную форму
    query_vec = tfidf_vectorizer.transform([query])
    
    # Рассчитываем косинусное сходство между запросом и всеми документами
    similarities = cosine_similarity(query_vec, tfidf_matrix).flatten()
    
    # Сортируем результаты по убыванию сходства
    top_indices = np.argsort(similarities)[::-1][:top_n]
    
    return top_indices, similarities[top_indices]

# Функция для поиска по BERT
def search_bert(query_embedding, bert_embeddings, top_n=5):
    # Рассчитываем косинусное сходство между запросом и всеми документами
    similarities = cosine_similarity([query_embedding], bert_embeddings).flatten()
    
    # Сортируем результаты по убыванию сходства
    top_indices = np.argsort(similarities)[::-1][:top_n]
    
    return top_indices, similarities[top_indices]

# Получение эмбеддингов BERT для запроса
def get_bert_embedding_for_query(query, tokenizer, model):
    inputs = tokenizer(query, return_tensors='pt', padding=True, truncation=True, max_length=512)
    with torch.no_grad():
        outputs = model(**inputs)
    cls_embedding = outputs.last_hidden_state[:, 0, :].squeeze().numpy()  # Используем CLS токен
    return cls_embedding

# Главная функция для выполнения поиска
def search_engine(query, index_choice, wiki_df, top_n=5):
    # Фиксируем время начала
    start_time = time.time()
    
    if index_choice == 'tf-idf':
        print("Используем TF-IDF для поиска...")
        top_indices, top_similarities = search_tfidf(query, tfidf_vectorizer, tfidf_matrix, top_n)
    elif index_choice == 'bert':
        print("Используем BERT для поиска...")
        tokenizer = BertTokenizer.from_pretrained('DeepPavlov/rubert-base-cased')
        model = BertModel.from_pretrained('DeepPavlov/rubert-base-cased')
        query_embedding = get_bert_embedding_for_query(query, tokenizer, model)
        top_indices, top_similarities = search_bert(query_embedding, bert_embeddings, top_n)
    
    else:
        print("Неверный вариант индекса. Выберите 'tf-idf' или 'bert'.")
        return
    
    # Фиксируем время завершения
    end_time = time.time()
    elapsed_time = end_time - start_time
    print(f"Поиск занял {elapsed_time:.4f} секунд.")
    
    # Выводим результаты
    print(f"Топ-{top_n} подходящих документов:")
    for i, idx in enumerate(top_indices):
        similarity = top_similarities[i]
        document_text = wiki_df['sample'].iloc[idx]  # Предполагаем, что 'sample' это колонка с текстами
        print(f"Сходство: {similarity:.4f}")
        print(f"Текст документа {idx}:\n{document_text}\n")
        
# Пример использования:
query = input("Введите текст запроса: ")
index_choice = input("Введите, какой вариант индекса использовать ('tf-idf' или 'bert'): ")

# Выполняем поиск и измеряем время
search_engine(query, index_choice, wiki_df)


Используем TF-IDF для поиска...
Поиск занял 0.0539 секунд.
Топ-5 подходящих документов:
Сходство: 0.1905
Текст документа 2293:
Колли  — группа пород пастушьих собак, происходящих из Шотландии и Северной Англии. Группа включает как официально признанные кинологическими организациями породы, так и малочисленные местные породы и отродья.Колли — пропорциональная собака среднего роста, достаточно лёгкого сложения, с заострённой мордой. Как правило, имеет характерную породную окраску. Колли активны, проворны и в большинстве случаев обладают ярко выраженным пастушьим инстинктом. Некоторые колли продолжают использоваться при выпасе крупного рогатого скота и овец. Другие содержатся в качестве компаньонов. Колли часто используются в кинологическом спорте, где они проявляют выдающиеся ловкость, выносливость и обучаемость.Колли широко распространены во всём мире, особенно популярны в Австралии и Северной Америке, где использовались для выведения других пастушьих пород, в том числе путём метизации 

#### **5. (1 балл) Описать в readme файле, как правильно запустить ваш код**

#### **6. (1 балл) Ваш код должен соотвествовать следующим критериям:**
- PEP8 и комментарии (для возможности оценки 10 - еще тайпинги и докстринги)
- Осмысленные имена переменных, функций, классов, модулей
- Разделение на модули (разные файлы для разных больших блоков логики) или объяснение, почему тут это пока не нужно
- Разделение на классы/функции
- Одна очевидная для пользователя точка входа: класс поисковика / функция запуска, куда потом можно подавать тексты запросов

✅ Выполнено на предыдущих этапах

#### **7. (1 балл) Реализовать оптимальную версию поиска: предварительно рассчитывается все, что можно посчитать заранее и сохранить, потом считать только то, что зависит от запроса (подсказка: возможно, вам придется написать функцию близости руками, чтобы это работало)**

✅ Выполнено на предыдущих этапах. Все засунула в функции, остается только выбрать вариант индекса и ввести запрос. 

#### **8. (1 балл) Реализовать CLI (вот тут можно почитать, через что их можно делать в питоне) или веб-интерфейс (Flask, Streamlit или что-то другое на ваш выбор). Опишите в ридми, как пользоваться вашим кодом (без этого балл не ставится)**

#### **9. (1 балл) Подумайте, как можно формально сравнить два способа индексации с точки зрения качества поиска и/или векторизации. Опишите, какой способ вы придумали, и используйте его для сравнения двух выбранных типов индексации.**

**Метрики для оценки информационного поиска:**
- Быстрота поиска
- Precision (точность) — доля релевантных документов среди всех найденных.
- Recall (полнота) — доля найденных релевантных документов среди всех возможных релевантных документов в корпусе.
- F1-метрика — гармоническое среднее между Precision и Recall.

**Процесс сравнения**
Шаг 1: Запустить несколько тестовых запросов и для каждого запроса вручную отметить несколько релевантных документов из базы.

Шаг 2: Запустить оба метода поиска (TF-IDF и BERT) с этими запросами и сохранить результат.

Шаг 3: Для каждого запроса и метода поиска сравнить полученные результаты с эталонным набором данных, рассчитав метрики Precision, Recall.

Шаг 4: Сравнить результаты между двумя методами по каждой метрике.

In [48]:
# Сет с тем, что мне показалось релевантным для обоих методов
relevance_set = {
    'маленькая пушистая собака, домашняя порода рыжего цвета': [2293, 4822, 3131],  
    'причины возникновения инфаркта миокарда': [2894, 5333, 3655],
    'перснальный компьютер для хранения, переработки информации и выхода в интернет': [2341, 751, 1944],
    'первые люди на Земле, сотворённые Богом и прародители человеческого рода' : [0, 6282, ]
}
#Сет для того, что выдал TF-IDF
search_results_tfidf = {
    'маленькая пушистая собака, домашняя порода рыжего цвета' : [2293, 4795, 5203, 4822, 3131],  
    'причины возникновения инфаркта миокарда': [0, 6283, 6282, 6281, 6280],
    'перснальный компьютер для хранения, переработки информации и выхода в интернет': [2341, 751, 1944, 2452, 2891],
    'первые люди на Земле, сотворённые Богом и прародители человеческого рода' : [0, 6283, 6282, 6281, 6280]
}
#Сет для того, что выдал bert
search_results_bert = {
    'маленькая пушистая собака, домашняя порода рыжего цвета' : [906, 3087, 2868, 5976, 767],  
    'ричины возникновения инфаркта миокарда': [2894, 3343, 5333, 3655, 2289],
    'перснальный компьютер для хранения, переработки информации и выхода в интернет': [2452, 751, 2495, 772, 3510],
    'первые люди на Земле, сотворённые Богом и прародители человеческого рода' : [4764, 4980, 5336, 3069, 4990]
}

# Функция для оценки Precision, Recall, F1
def evaluate_search(results, relevance_set):
    precision_scores = []
    recall_scores = []
    f1_scores = []
    
    for query, relevant_docs in relevance_set.items():
        predicted_docs = results.get(query, [])
        
        # Создаем бинарный вектор релевантности (1 - релевантен, 0 - не релевантен)
        relevant_labels = [1 if doc_id in relevant_docs else 0 for doc_id in predicted_docs]
        predicted_labels = [1] * len(predicted_docs)  # Все результаты предсказаны как релевантные

        # Рассчитываем метрики
        precision = precision_score(relevant_labels, predicted_labels, average='binary')
        recall = recall_score(relevant_labels, predicted_labels, average='binary')
        f1 = f1_score(relevant_labels, predicted_labels, average='binary')
        
        precision_scores.append(precision)
        recall_scores.append(recall)
        f1_scores.append(f1)

    # Средние значения метрик
    avg_precision = sum(precision_scores) / len(precision_scores)
    avg_recall = sum(recall_scores) / len(recall_scores)
    avg_f1 = sum(f1_scores) / len(f1_scores)
    
    return avg_precision, avg_recall, avg_f1

# Оценка для TF-IDF
precision_tfidf, recall_tfidf, f1_tfidf = evaluate_search(search_results_tfidf, relevance_set)
print(f"TF-IDF - Precision: {precision_tfidf}, Recall: {recall_tfidf}, F1: {f1_tfidf}")

# Оценка для BERT
precision_bert, recall_bert, f1_bert = evaluate_search(search_results_bert, relevance_set)
print(f"BERT - Precision: {precision_bert}, Recall: {recall_bert}, F1: {f1_bert}")

TF-IDF - Precision: 0.4, Recall: 0.75, F1: 0.5178571428571428
BERT - Precision: 0.05, Recall: 0.25, F1: 0.08333333333333333


C:\Users\Zaxarova\AppData\Roaming\Python\Python310\site-packages\sklearn\metrics\_classification.py:1531: UndefinedMetricWarning: Recall is ill-defined and being set to 0.0 due to no true samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, f"{metric.capitalize()} is", len(result))
C:\Users\Zaxarova\AppData\Roaming\Python\Python310\site-packages\sklearn\metrics\_classification.py:1531: UndefinedMetricWarning: Recall is ill-defined and being set to 0.0 due to no true samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, f"{metric.capitalize()} is", len(result))
C:\Users\Zaxarova\AppData\Roaming\Python\Python310\site-packages\sklearn\metrics\_classification.py:1531: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 due to no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, f"{metric.capitalize()} is", len(result))
C:\Users\Zaxar

Вот итоги кода выше: 

```TF-IDF - Precision: 0.4, Recall: 0.75, F1: 0.5178571428571428```

```BERT - Precision: 0.05, Recall: 0.25, F1: 0.08333333333333333```

Результаты показывают, что TF-IDF справляется лучше, чем Bert. Однако, это все еще зависит от того, что я посчитаю релевантным, а что нет. 

##### Про время: 
<div style="display: flex;">

<div style="flex: 1; padding-right: 10px;">

**TF-IDF:**

- Запрос про собаку - Поиск занял 0.0549 секунд.
- Запрос про инфаркт - Поиск занял 0.0509 секунд.
- Запрос про пк - Поиск занял 0.0539 секунд.
- Запрос про Адама и Еву - Поиск занял 0.0598 секунд.

**СРЗНАЧ = 0.05488**

</div>

<div style="flex: 1; padding-left: 10px;">

**Bert:**

- Запрос про собаку - Поиск занял 3.0259 секунд.
- Запрос про инфаркт - Поиск занял 1.3189 секунд.
- Запрос про пк - Поиск занял 1.7085 секунд.
- Запрос про Адама и Еву - Поиск занял 1.1532 секунд.

**СРЗНАЧ = 1.80163**

</div>

</div>


=> По этому критерию также выигрывает TF-IDF